In [2]:
import pandas as pd
import numpy as np
import spacy

In [3]:
import en_ner_bc5cdr_md
import en_core_med7_lg

In [4]:
# To install spaCy's pre-trained model en_ner_bc5cdr_md, en_core_med7_lg use the link below. You can also install the transformer

# !pip install https://s3-us-west-2.amazonaws.com/ai2-s2-scispacy/releases/v0.5.1/en_ner_bc5cdr_md-0.5.1.tar.gz
# !pip install https://huggingface.co/kormilitzin/en_core_med7_trf/resolve/main/en_core_med7_trf-any-py3-none-any.whl --user
# !pip install https://huggingface.co/kormilitzin/en_core_med7_lg/resolve/main/en_core_med7_lg-any-py3-none-any.whl --user

In [5]:
med = pd.read_csv('mtsamples.csv', index_col=0)
med.head()

description  \
0   A 23-year-old white female presents with comp...   
1           Consult for laparoscopic gastric bypass.   
2           Consult for laparoscopic gastric bypass.   
3                             2-D M-Mode. Doppler.     
4                                 2-D Echocardiogram   

             medical_specialty                                sample_name  \
0         Allergy / Immunology                         Allergic Rhinitis    
1                   Bariatrics   Laparoscopic Gastric Bypass Consult - 2    
2                   Bariatrics   Laparoscopic Gastric Bypass Consult - 1    
3   Cardiovascular / Pulmonary                    2-D Echocardiogram - 1    
4   Cardiovascular / Pulmonary                    2-D Echocardiogram - 2    

                                       transcription  \
0  SUBJECTIVE:,  This 23-year-old white female pr...   
1  PAST MEDICAL HISTORY:, He has difficulty climb...   
2  HISTORY OF PRESENT ILLNESS: , I have seen ABC ...   
3  2-D M-MODE: , ,1.  Left atrial enlargement wit...   
4  1.  The left ventricular cavity size and wall ...   

                                            keywords  
0  allergy / immunology, allergic rhinitis, aller...  
1  bariatrics, laparoscopic gastric bypass, weigh...  
2  bariatrics, laparoscopic gastric bypass, heart...  
3  cardiovascular / pulmonary, 2-d m-mode, dopple...  
4  cardiovascular / pulmonary, 2-d, doppler, echo...

In [6]:
med.isnull().sum()

description             0
medical_specialty       0
sample_name             0
transcription          33
keywords             1068
dtype: int64

In [7]:
med.shape

(4999, 5)

In [8]:
med.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 4999 entries, 0 to 4998
Data columns (total 5 columns):
 #   Column             Non-Null Count  Dtype 
---  ------             --------------  ----- 
 0   description        4999 non-null   object
 1   medical_specialty  4999 non-null   object
 2   sample_name        4999 non-null   object
 3   transcription      4966 non-null   object
 4   keywords           3931 non-null   object
dtypes: object(5)
memory usage: 234.3+ KB


In [9]:
import re

med['transcription'] = med['transcription'].astype('str')
med['transcription'] = med['transcription'].apply(lambda x: re.sub('(\.,)', ". ", x))

In [10]:
nlp = spacy.load("en_core_med7_lg")

# This function generate anotation for each entities and label
def generate_annotation(texts):
    annotations = []
    for text in texts:
        doc = nlp(text)
        entities = []
        for ent in doc.ents:
            entities.append((ent.start_char, ent.end_char, ent.label_))
        annotations.append((text, {'entities': entities}))
    return annotations

# Extract text entities and labels from the dataset (transcription)
medical_doc = med['transcription'].tolist()

# Let's generate annotations
annotations = generate_annotation(medical_doc)

# Let's print documents and annotations
print("Document:")
print(annotations[0][0]) # first document text
print("Annotations:")
print(annotations[0][1]) # annotation for the first document

Document:
SUBJECTIVE:,  This 23-year-old white female presents with complaint of allergies.  She used to have allergies when she lived in Seattle but she thinks they are worse here.  In the past, she has tried Claritin, and Zyrtec.  Both worked for short time but then seemed to lose effectiveness.  She has used Allegra also.  She used that last summer and she began using it again two weeks ago.  It does not appear to be working very well.  She has used over-the-counter sprays but no prescription nasal sprays.  She does have asthma but doest not require daily medication for this and does not think it is flaring up. MEDICATIONS: , Her only medication currently is Ortho Tri-Cyclen and the Allegra. ALLERGIES: , She has no known medicine allergies. OBJECTIVE:,Vitals:  Weight was 130 pounds and blood pressure 124/78. HEENT:  Her throat was mildly erythematous without exudate.  Nasal mucosa was erythematous and swollen.  Only clear drainage was seen.  TMs were clear. Neck:  Supple without ade

In [ ]:
#med['annotation'] = med['transcription'].apply(lambda x:generate_annotation(x))

In [33]:
from spacy import displacy
nlp = spacy.load("en_core_med7_lg")

# Create distict colours for labels

col_dict = {}
s_colours = ['#e6194B', '#3cb44b', '#ffe119', '#ffd8b1', '#f58231', '#f032e6', '#42d4f4']
for label, colour in zip(nlp.pipe_labels['ner'], s_colours):
    col_dict[label] = colour

options = {'ents': nlp.pipe_labels['ner'], 'colors':col_dict}

transcription = med['transcription'][0]
doc = nlp(transcription)

spacy.displacy.render(doc, style = 'ent', jupyter = True, options = options)

[(ent.text, ent.label_) for ent in doc.ents]

[('Claritin', 'DRUG'),
 ('Zyrtec', 'DRUG'),
 ('daily', 'FREQUENCY'),
 ('Zyrtec', 'DRUG'),
 ('loratadine', 'DRUG'),
 ('Nasonex', 'DRUG'),
 ('two', 'DOSAGE'),
 ('sprays', 'FORM'),
 ('each', 'DOSAGE'),
 ('for three weeks', 'DURATION')]

In [25]:
med_adj = med.sample(n=111, replace = False, random_state=42)

In [21]:
nlp = spacy.load("en_ner_bc5cdr_md")

transcription = med['transcription'].iloc[1]
doc= nlp(transcription)

# Let's extract and print all the entity
for ent in doc.ents:
    print(f"Text: {ent.text}, Entity Type: {ent.label_}")
    #print(f"Text: {ent.text}, Start: {ent.start_char}, End: {ent.end_char}, Entity Type: {ent.label_}") you can also use this

Text: snoring, Entity Type: DISEASE
Text: pains, Entity Type: DISEASE
Text: knee pain, Entity Type: DISEASE
Text: pain, Entity Type: DISEASE
Text: ankle pain, Entity Type: DISEASE
Text: gastroesophageal reflux disease, Entity Type: DISEASE
Text: Heart disease, Entity Type: DISEASE
Text: stroke, Entity Type: DISEASE
Text: diabetes, Entity Type: DISEASE
Text: obesity, Entity Type: DISEASE
Text: hypertension, Entity Type: DISEASE
Text: allergic, Entity Type: DISEASE
Text: Penicillin, Entity Type: CHEMICAL
Text: chest pain, Entity Type: DISEASE
Text: coronary artery disease, Entity Type: DISEASE
Text: congestive heart failure, Entity Type: DISEASE
Text: arrhythmia, Entity Type: DISEASE
Text: atrial fibrillation, Entity Type: DISEASE
Text: cholesterol, Entity Type: CHEMICAL
Text: pulmonary embolism, Entity Type: DISEASE
Text: CVA, Entity Type: CHEMICAL
Text: venous insufficiency, Entity Type: DISEASE
Text: thrombophlebitis, Entity Type: DISEASE
Text: asthma, Entity Type: DISEASE
Text: short

In [26]:
from  spacy.matcher import Matcher

# Let's load the model
nlp = spacy.load("en_core_med7_lg")

patterns = [
    [{"ENT_TYPE": "DRUG"}, {"LIKE_NUM": True}, {"IS_ASCII": True}],
    [{"LOWER": {"IN": ["mg", "g", "ml"]}}, {"ENT_TYPE": "DRUG"}],
    [{"ENT_TYPE": "DRUG"}, {"IS_DIGIT": True, "OP": "?"}, {"LOWER": {"IN": ["mg", "g", "ml"]}}]
]

matcher = Matcher(nlp.vocab)
matcher.add("DRUG_DOSE", patterns)

for transcription in  med_adj['transcription']:
    doc = nlp(transcription)
    matches = matcher(doc)
    for match_id, start, end in matches:
        string_id = nlp.vocab.strings[match_id]
        span = doc[start:end]
        print(string_id, start, end, span.text)


DRUG_DOSE 514 517 Diastat 20 mg
DRUG_DOSE 518 521 Topamax 25 mg
DRUG_DOSE 532 535 Tranxene 15 mg
DRUG_DOSE 538 541 Depakote 125 mg
DRUG_DOSE 729 732 Depacon 250 mg
DRUG_DOSE 266 269 Pepcid 40 mg
DRUG_DOSE 109 112 furosemide 40 mg
DRUG_DOSE 897 900 diltiazem 120 mg
DRUG_DOSE 433 436 Aspirin 325 mg
DRUG_DOSE 443 446 Lisinopril 40 mg
DRUG_DOSE 453 456 Felodipine 10 mg
DRUG_DOSE 465 468 Con 20 mEq
DRUG_DOSE 475 478 Omeprazole 20 mg
DRUG_DOSE 488 491 MiraLax 17 g
DRUG_DOSE 498 501 Lasix 20 mg
DRUG_DOSE 282 285 Omeprazole 40 mg
DRUG_DOSE 25 28 Prozac 20 mg
DRUG_DOSE 274 277 Rocephin 250 mg
DRUG_DOSE 278 281 azithromycin 1000 mg
DRUG_DOSE 504 507 Coumadin 5 mg
DRUG_DOSE 524 527 Aspirin 81 mg
DRUG_DOSE 533 536 Hydrochlorothiazide 25 mg
DRUG_DOSE 542 545 Plendil 10 mg
DRUG_DOSE 550 553 Lipitor 40 mg
DRUG_DOSE 955 958 dexamethasone 4 mg
DRUG_DOSE 286 289 Plavix 75 mg
DRUG_DOSE 294 297 metoprolol 25 mg
DRUG_DOSE 302 305 Flomax 0.4 mg
DRUG_DOSE 310 313 Zocor 20 mg
DRUG_DOSE 327 330 lisinopril 10 m

In [34]:
med_adj = med.sample(n=3, replace = False, random_state=42)

In [ ]:
# Let's load our pretrained spacy model

nlp = spacy.load("en_core_med7_lg")

# this function will extract relevant entities and labels needed from medical transcription 

def extract_keywords(text):
    doc = nlp(text)
    entities = []
    entities = [(ent.text, ent.label_) for ent in doc.ents]
    return entities

# Lets define our categories
surgery_keywords = ["surgery", "operation", "procedure", "acute Cholangitis", "surgisis", "appendicitis"]
cardio_pul_keywords = ["heart", "cardiovascular", "pulmonary", "lungs"]
orthopaedic_keywords = ["orthopaedic", "bone", "joint", "fracture"]
neurology_keywords = ["neurology", "nervours system", "brain", "nerve"]
general_med_keywords = ["patient", "complaining", "history", "medical"]
    
# This will process each medical description and check for relevant keywords
medical_doc = med['transcription']
for transcription in medical_doc:
    entities = extract_keywords(transcription.lower())
    
    is_surgery = any(keyword in transcription.lower() for keyword in surgery_keywords)
    is_cardio_pul = any(keyword in transcription.lower() for keyword in cardio_pul_keywords)
    is_orthopaedic = any(keyword in transcription.lower() for keyword in orthopaedic_keywords)
    is_neurology = any(keyword in transcription.lower() for keyword in neurology_keywords)
    is_general_med = any(keyword in transcription.lower() for keyword in general_med_keywords)
    
    print("Transcription:", transcription)
    print("Entities:", entities)
    print("Is Surgery:", is_surgery)
    print("Is Cardio Pulmonary:", is_cardio_pul)
    print("Orthopaedic:", is_orthopaedic)
    print("Neurology:", is_neurology)
    print("General Medicine:", is_general_med)